In [1]:
#import numpy
import sys
from nltk.tokenize import RegexpTokenizer
from nltk.corpus import stopwords
from keras.models import Sequential
from keras.layers import Dense, Dropout, LSTM
from keras.utils import np_utils
from keras.callbacks import ModelCheckpoint

import pandas as pd
import numpy as np
import nltk
nltk.download('stopwords', quiet=True)
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer 
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import confusion_matrix, plot_confusion_matrix
naive_bayes_classifier = MultinomialNB()

In [2]:
from google.colab import files
import io
uploaded_item = files.upload()

Saving Motivational Quotes Database.csv to Motivational Quotes Database.csv


In [3]:
 # Read in csv
df = pd.read_csv('Motivational Quotes Database.csv', encoding = "ISO-8859-1")
df.rename(columns = {'Motivational Quotes Database - https://www.sharpquotes.com':'Quotes'}, inplace = True)
#quotes = df.pop("Quotes")


df = df.tail(45575)
#quotes = quotes.str.lower()
filtered = df["Quotes"].to_string()

#tokenizer = RegexpTokenizer(r'\w+')
#tokens = tokenizer.tokenize(quotes["Quotes"])

#stop = stopwords.words('english')
#quotes.apply(lambda x: [item for item in x if item not in stop])
#quotes = quotes["Quotes"].to_string())
#filtered.replace('\n', ' ')

In [4]:
filtered

'        Age is an issue of mind over matter. If you do...\n        Anyone who stops learning is old, whether at t...\n        Wrinkles should merely indicate where smiles h...\n        True terror is to wake up one morning and disc...\n        A diplomat is a man who always remembers a wom...\n        As I grow older, I pay less attention to what ...\n        How incessant and great are the ills with whic...\n       Old age, believe me, is a good and pleasant th...\n       Old age has deformities enough of its own. It ...\n       Nobody grows old merely by living a number of ...\n       An archaeologist is the best husband a woman c...\n                     All diseases run into one, old age.\n       Bashfulness is an ornament to youth, but a rep...\n       Like everyone else who makes the mistake of ge...\n       Age appears to be best in four things old wood...\n       None are so old as those who have outlived ent...\n                    Every man over forty is a scoundrel.\n      

In [5]:
#filtered = filtered.replace('\n\d+', ' ')#removes "\n"
#filtered = filtered.replace(r'^\d+\.\s+','') #removes numbers
#tokenizer = RegexpTokenizer('\w+')
#tokens = tokenizer.tokenize(filtered.lower())
#filtered = filter(lambda token: token not in stopwords.words('english'), tokens)

In [5]:
#processing data
filtered = ''.join([i for i in filtered if not i.isdigit()])
filtered = filtered.lower()


# instantiate the tokenizer
tokenizer = RegexpTokenizer(r'\w+')
filtered = tokenizer.tokenize(filtered)

# if the created token isn't in the stop words, make it part of "filtered"
#filtered = filter(lambda token: token not in stopwords.words('english'), tokens)

In [6]:
filtered = " ".join(filtered)

In [7]:
filtered

'age is an issue of mind over matter if you do anyone who stops learning is old whether at t wrinkles should merely indicate where smiles h true terror is to wake up one morning and disc a diplomat is a man who always remembers a wom as i grow older i pay less attention to what how incessant and great are the ills with whic old age believe me is a good and pleasant th old age has deformities enough of its own it nobody grows old merely by living a number of an archaeologist is the best husband a woman c all diseases run into one old age bashfulness is an ornament to youth but a rep like everyone else who makes the mistake of ge age appears to be best in four things old wood none are so old as those who have outlived ent every man over forty is a scoundrel forty is the old age of youth fifty the youth you can t help getting older but you don t ha alas after a certain age every man is respons youth is when you re allowed to stay up late o old age is like everything else to make a suc a c

#All code below was taken from https://stackabuse.com/text-generation-with-python-and-tensorflow-keras/
#slight modifications to better suit this project


In [8]:
# create mapping
chars = sorted(list(set(filtered)))
char_to_num = dict((c, i) for i, c in enumerate(chars))

In [9]:
input_len = len(filtered)
vocab_len = len(chars)
print ("Total number of characters:", input_len)
print ("Total vocab:", vocab_len)

Total number of characters: 2075075
Total vocab: 27


In [10]:
# prepare the dataset
seq_length = 100
x_data = []
y_data = []

In [11]:
for i in range(0, input_len - seq_length, 1):
  in_seq = filtered[i:i + seq_length]
  out_seq = filtered[i + seq_length]
  x_data.append([char_to_num[char] for char in in_seq])
  y_data.append(char_to_num[out_seq])

In [12]:
n_patterns = len(x_data)
print ("Total Patterns:", n_patterns)

Total Patterns: 2074975


In [13]:
# reshape X and normalize
X = np.reshape(x_data, (n_patterns, seq_length, 1))
X = X/float(vocab_len)

In [14]:
# one hot encode
y = np_utils.to_categorical(y_data)

In [15]:
# define LSTM model
model = Sequential()
model.add(LSTM(256, input_shape=(X.shape[1], X.shape[2]), return_sequences=True))
model.add(Dropout(0.2))
model.add(LSTM(256, return_sequences=True))
model.add(Dropout(0.2))
model.add(LSTM(128))
model.add(Dropout(0.2))
model.add(Dense(y.shape[1], activation='softmax'))

In [16]:
# load network weights, use "adam"
model.compile(loss='categorical_crossentropy', optimizer='adam')

In [17]:
filepath = "model_weights_saved.hdf5"
checkpoint = ModelCheckpoint(filepath, monitor='loss', verbose=1, save_best_only=True, mode='min')
desired_callbacks = [checkpoint]

In [18]:
model.fit(X, y, epochs=20, batch_size=256, callbacks=desired_callbacks)

Epoch 1/20
8106/8106 [==============================] - 328s 38ms/step - loss: 2.3564

Epoch 00001: loss improved from inf to 2.06992, saving model to model_weights_saved.hdf5
Epoch 2/20
8106/8106 [==============================] - 307s 38ms/step - loss: 1.7348

Epoch 00002: loss improved from 2.06992 to 1.70082, saving model to model_weights_saved.hdf5
Epoch 3/20
8106/8106 [==============================] - 308s 38ms/step - loss: 1.6211

Epoch 00003: loss improved from 1.70082 to 1.60770, saving model to model_weights_saved.hdf5
Epoch 4/20
8106/8106 [==============================] - 308s 38ms/step - loss: 1.5665

Epoch 00004: loss improved from 1.60770 to 1.55710, saving model to model_weights_saved.hdf5
Epoch 5/20
8106/8106 [==============================] - 307s 38ms/step - loss: 1.5303

Epoch 00005: loss improved from 1.55710 to 1.52397, saving model to model_weights_saved.hdf5
Epoch 6/20
8106/8106 [==============================] - 307s 38ms/step - loss: 1.5026

Epoch 00006: loss

In [19]:
#loads weights
filename = "model_weights_saved.hdf5"
model.load_weights(filename)
model.compile(loss='categorical_crossentropy', optimizer='adam')

In [20]:
num_to_char = dict((i, c) for i, c in enumerate(chars))

In [33]:
#uses random seed
start = np.random.randint(0, len(x_data) - 1)
pattern = x_data[start]
print("Random Seed:")
print("\"", ''.join([num_to_char[value] for value in pattern]), "\"")

Random Seed:
" backward look ahead we re at the crossroads down one road is a eu children are not casual guests in  "


In [34]:
for i in range(100):
    x = np.reshape(pattern, (1, len(pattern), 1))
    x = x / float(vocab_len)
    prediction = model.predict(x, verbose=0)
    index = np.argmax(prediction)
    result = num_to_char[index]

    sys.stdout.write(result)

    pattern.append(index)
    pattern = pattern[1:len(pattern)]

the morning i don t have the more than the more than the more than the more than the more than the m